In [1]:
import sys
sys.path.extend(['../', '../read_utils/'])

import json
import numpy as np
from pathlib import Path

from read_utils.main import (
    calibrate_magnetic_wifi_ibeacon_to_position, 
    extract_wifi_rssi, 
    visualize_heatmap, 
    save_figure_to_html,
)


In [2]:
floor_data_dir = '../data/site1/F1'
path_data_dir = floor_data_dir + '/path_data_files'
floor_plan_filename = floor_data_dir + '/floor_image.png'
floor_info_filename = floor_data_dir + '/floor_info.json'

save_dir = '../output/site1/F1'
wifi_image_save_dir = save_dir + '/wifi_images'

In [3]:
with open(floor_info_filename) as f:
    floor_info = json.load(f)
width_meter = floor_info["map_info"]["width"]
height_meter = floor_info["map_info"]["height"]
print(width_meter, height_meter)

path_filenames = list(Path(path_data_dir).resolve().glob("*.txt"))
mwi_datas = calibrate_magnetic_wifi_ibeacon_to_position(path_filenames)
step_positions = np.array(list(mwi_datas.keys()))
print(step_positions.shape)

239.81749314504376 176.44116534000818
(7840, 2)


In [8]:
# WiFi APs = WiFi access points
# RSS = Received Signal Strength / RSSI = Received Signal Strength Indicator
# BSSID = Basic Service Set Identifier 
wifi_rssi = extract_wifi_rssi(mwi_datas)
print(len(wifi_rssi))
print(list(wifi_rssi.keys())[:5])
print(list(wifi_rssi.keys())[-5:])

2524
['06:74:9c:a7:a3:c0', '0a:74:9c:a7:a3:c0', '16:74:9c:a7:a3:c0', '0e:74:9c:a7:a3:c0', '1e:74:9c:a7:a3:c0']
['12:74:9c:2b:55:9f', '0e:74:9c:2d:11:fa', 'd8:32:14:6a:a2:01', '48:7d:2e:94:1b:62', '78:44:fd:77:08:a2']


In [22]:
print([k for k, v in sorted(wifi_rssi.items(), key=lambda item: len(item[1]), reverse=True)][:5])

['12:74:9c:a7:a3:c0', '16:74:9c:a7:a3:c0', '0a:74:9c:a7:a3:c0', '0e:74:9c:a7:a3:c0', '1e:74:9c:a7:a3:c0']


In [24]:
def inverse_distance_weighting(known_points, known_values, unknown_points, power=2):
    """
    Interpolate using Inverse Distance Weighting.
    """
    interpolated_values = []
    for point in unknown_points:
        # Compute distances to known_points
        distances = np.linalg.norm(known_points - point, axis=1)
        # Avoid divide by zero
        distances[distances == 0] = 1e-5
        # Compute weights
        weights = 1.0 / distances**power
        # Compute weighted average
        value = np.sum(weights * known_values) / np.sum(weights)
        interpolated_values.append(value)
    return np.array(interpolated_values)


for target_wifi in ['12:74:9c:a7:a3:c0', '16:74:9c:a7:a3:c0', '0a:74:9c:a7:a3:c0']:
    heat_positions = np.array(list(wifi_rssi[target_wifi].keys()))
    heat_values = np.array(list(wifi_rssi[target_wifi].values()))[:, 0]
    print(heat_positions.shape, heat_values.shape)

    fig = visualize_heatmap(
        heat_positions, 
        heat_values, 
        floor_plan_filename, 
        width_meter, 
        height_meter, 
        colorbar_title='dBm', 
        title=f'Wifi: {target_wifi} RSSI', 
        show=True,
    )
    html_filename = f'{wifi_image_save_dir}/{target_wifi.replace(":", "-")}.html'
    html_filename = str(Path(html_filename).resolve())
    save_figure_to_html(fig, html_filename)

    # Extract the missing positions
    missing_positions_mask = np.isin(step_positions, heat_positions).all(axis=1)    
    missing_positions = step_positions[~missing_positions_mask]
    print(missing_positions.shape)

    all_positions = np.vstack([heat_positions, missing_positions])

    # Interpolate using Inverse Distance Weighting (IDW)
    idw_interpolated_values = inverse_distance_weighting(heat_positions, heat_values, missing_positions)
    print(idw_interpolated_values.shape)

    all_idw_values = np.hstack([heat_values, idw_interpolated_values])

    fig = visualize_heatmap(
        all_positions, 
        all_idw_values, 
        floor_plan_filename, 
        width_meter, 
        height_meter, 
        colorbar_title='dBm', 
        title=f'Wifi: {target_wifi} RSSI', 
        show=True,
    )
    html_filename = f'{wifi_image_save_dir}/{target_wifi.replace(":", "-")}-idw.html'
    html_filename = str(Path(html_filename).resolve())
    save_figure_to_html(fig, html_filename)

(1561, 2) (1561,)


(6279, 2)
(6279,)


(1557, 2) (1557,)


(6283, 2)
(6283,)


(1553, 2) (1553,)


(6287, 2)
(6287,)
